In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from IPython.display import display

pd.options.display.max_columns = None
pd.options.display.max_rows = 1000

%matplotlib inline

In [2]:

shots = pd.read_csv("../shotcharts-2018-19.csv")
pbp = pd.read_csv("../pbp-2018-19.csv")

In [3]:
pbp.tail(100)

Unnamed: 0   GAME_ID  EVENTNUM  EVENTMSGTYPE  EVENTMSGACTIONTYPE  \
235348         338  21800496       509             8                   0   
235349         339  21800496       511             2                   1   
235350         340  21800496       512             4                   0   
235351         341  21800496       513             1                  41   
235352         342  21800496       515             6                   2   
235353         343  21800496       517             3                  11   
235354         344  21800496       518             3                  12   
235355         345  21800496       519             1                  79   
235356         346  21800496       520             5                   1   
235357         347  21800496       522             2                  98   
235358         348  21800496       524             4                   0   
235359         349  21800496       525             1                  76   
235360         350  21800496       527             6                   2   
235361         351  21800496       529             8                   0   
235362         352  21800496       531             3                  10   
235363         353  21800496       532             2                  78   
235364         354  21800496       533             4                   0   
235365         355  21800496       535             5                  11   
235366         356  21800496       536             5                  39   
235367         357  21800496       537             2                   1   
235368         358  21800496       538             4                   0   
235369         359  21800496       539             2                   6   
235370         360  21800496       540             4                   0   
235371         361  21800496       541             2                   5   
235372         362  21800496       543             4                   0   
235373         363  21800496       544             1                  80   
235374         364  21800496       545             1                   1   
235375         365  21800496       547             1                   1   
235376         366  21800496       549             2                  98   
235377         367  21800496       551             4                   0   
235378         368  21800496       552             5                   1   
235379         369  21800496       554             1                  50   
235380         370  21800496       555             9                   1   
235381         371  21800496       556             8                   0   
235382         372  21800496       557             8                   0   
235383         373  21800496       558             8                   0   
235384         374  21800496       559             8                   0   
235385         375  21800496       564             1                   1   
235386         376  21800496       565             2                   1   
235387         377  21800496       566             4                   0   
235388         378  21800496       567             2                  78   
235389         379  21800496       569             4                   0   
235390         380  21800496       570             2                  97   
235391         381  21800496       571             4                   0   
235392         382  21800496       572             1                  98   
235393         383  21800496       574             6                   2   
235394         384  21800496       576             3                  11   
235395         385  21800496       577             8                   0   
235396         386  21800496       579             3                  12   
235397         387  21800496       580             4                   0   
235398         388  21800496       581             2                  43   
235399         389  21800496       582             4    

In [4]:
shots.head()

Unnamed: 0          GRID_TYPE   GAME_ID  GAME_EVENT_ID  PLAYER_ID  \
0           0  Shot Chart Detail  21800001            114     201143   
1           1  Shot Chart Detail  21800001            271     201143   
2           2  Shot Chart Detail  21800001            308     201143   
3           3  Shot Chart Detail  21800001            353     201143   
4           4  Shot Chart Detail  21800001            580     201143   

  PLAYER_NAME     TEAM_ID       TEAM_NAME  PERIOD  MINUTES_REMAINING  \
0  Al Horford  1610612738  Boston Celtics       1                  3   
1  Al Horford  1610612738  Boston Celtics       2                  5   
2  Al Horford  1610612738  Boston Celtics       2                  2   
3  Al Horford  1610612738  Boston Celtics       3                 11   
4  Al Horford  1610612738  Boston Celtics       4                  7   

   SECONDS_REMAINING   EVENT_TYPE                     ACTION_TYPE  \
0                 47    Made Shot              Driving Layup Shot   
1                  7    Made Shot            Alley Oop Layup shot   
2                 24    Made Shot  Driving Finger Roll Layup Shot   
3                  5    Made Shot                       Jump Shot   
4                 24  Missed Shot              Fadeaway Jump Shot   

        SHOT_TYPE        SHOT_ZONE_BASIC SHOT_ZONE_AREA  SHOT_ZONE_RANGE  \
0  2PT Field Goal        Restricted Area      Center(C)  Less Than 8 ft.   
1  2PT Field Goal        Restricted Area      Center(C)  Less Than 8 ft.   
2  2PT Field Goal        Restricted Area      Center(C)  Less Than 8 ft.   
3  2PT Field Goal              Mid-Range   Left Side(L)         8-16 ft.   
4  2PT Field Goal  In The Paint (Non-RA)      Center(C)  Less Than 8 ft.   

   SHOT_DISTANCE  LOC_X  LOC_Y  SHOT_ATTEMPTED_FLAG  SHOT_MADE_FLAG  \
0              2     24     -1                    1               1   
1              1     -2     11                    1               1   
2              1     -9      7                    1               1   
3             12   -114     53                    1               1   
4              6     40     57                    1               0   

   GAME_DATE  HTM  VTM  
0   20181016  BOS  PHI  
1   20181016  BOS  PHI  
2   20181016  BOS  PHI  
3   20181016  BOS  PHI  
4   20181016  BOS  PHI

### Filter pbp data for OREB
1. Start by shifting `HOMEDESCRIPTION` and `VISITORDESCRIPTION` to get the next play and create two new columns, `next_Home_desc` and `next_Visitor_desc`
2. Create a new column `creates_OREB` and filter for current description contains `MISS` and next description contains `REBOUND`. 1 if true and 0 if false so that can easily sum to get counts later.
3. Get `three_next`, `four_next`, etc... to attempt to gather points off OREB for shots and FT

In [42]:
pbp['next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-1)
pbp['next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-1)

pbp['two_next_play_event_type'] = pbp['EVENTMSGTYPE'].shift(-2)
pbp['two_next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-2)
pbp['two_next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-2)

pbp['three_next_play_event_type'] = pbp['EVENTMSGTYPE'].shift(-3)
pbp['three_next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-3)
pbp['three_next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-3)

pbp['four_next_play_event_type'] = pbp['EVENTMSGTYPE'].shift(-4)
pbp['four_next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-4)
pbp['four_next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-4)

pbp['five_next_play_event_type'] = pbp['EVENTMSGTYPE'].shift(-5)
pbp['five_next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-5)
pbp['five_next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-5)

pbp['six_next_play_event_type'] = pbp['EVENTMSGTYPE'].shift(-6)
pbp['six_next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-6)
pbp['six_next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-6)

pbp['seven_next_play_event_type'] = pbp['EVENTMSGTYPE'].shift(-7)
pbp['seven_next_Home_desc'] = pbp['HOMEDESCRIPTION'].shift(-7)
pbp['seven_next_Visitor_desc'] = pbp['VISITORDESCRIPTION'].shift(-7)

Conditionally set OREB, OREB outcomes type, and points from OREB 

In [43]:
pbp['creates_OREB'] = np.where(((pbp.next_Home_desc.str.contains('REBOUND'))&(pbp.HOMEDESCRIPTION.str.contains('MISS'))) |
                                ((pbp.next_Visitor_desc.str.contains('REBOUND'))&(pbp.VISITORDESCRIPTION.str.contains('MISS')))
                                 ,
                                1,
                                0
                                )

pbp['OREB_outcome'] = np.where((pbp.creates_OREB == 1)&(pbp.two_next_play_event_type == 1),
                               1,
                               np.where((pbp.creates_OREB == 1)&(pbp.two_next_play_event_type == 6),
                                        6,
                                        0))
pbp['FT1'] = np.where(pbp.OREB_outcome == 6,
                     np.where(((pbp.three_next_play_event_type == 3) & np.logical_not(pbp.three_next_Home_desc.str.contains('MISS')) 
                               & (pd.notnull(pbp.HOMEDESCRIPTION))) |
                              ((pbp.three_next_play_event_type == 3) & np.logical_not(pbp.three_next_Visitor_desc.str.contains('MISS'))
                               & (pd.notnull(pbp.VISITORDESCRIPTION))),
                             1,
                             0),
                      0
                      
                     )

pbp['FT2'] = np.where(pbp.OREB_outcome == 6,
                     np.where(((pbp.four_next_play_event_type == 3) & np.logical_not(pbp.four_next_Home_desc.str.contains('MISS')) 
                               & (pd.notnull(pbp.HOMEDESCRIPTION))) |
                              ((pbp.four_next_play_event_type == 3) & np.logical_not(pbp.four_next_Visitor_desc.str.contains('MISS'))
                               & (pd.notnull(pbp.VISITORDESCRIPTION))),
                             1,
                             0),
                      0
                      
                     )
pbp['FT3'] = np.where(pbp.OREB_outcome == 6,
                     np.where(((pbp.five_next_play_event_type == 3) & np.logical_not(pbp.five_next_Home_desc.str.contains('MISS')) 
                               & (pd.notnull(pbp.HOMEDESCRIPTION))) |
                              ((pbp.five_next_play_event_type == 3) & np.logical_not(pbp.five_next_Visitor_desc.str.contains('MISS'))
                               & (pd.notnull(pbp.VISITORDESCRIPTION))),
                             1,
                             0),
                      0
                      
                     )

pbp['FT4'] = np.where(pbp.OREB_outcome == 6,
                     np.where(((pbp.six_next_play_event_type == 3) & np.logical_not(pbp.six_next_Home_desc.str.contains('MISS')) 
                               & (pd.notnull(pbp.HOMEDESCRIPTION))) |
                              ((pbp.six_next_play_event_type == 3) & np.logical_not(pbp.six_next_Visitor_desc.str.contains('MISS'))
                               & (pd.notnull(pbp.VISITORDESCRIPTION))),
                             1,
                             0),
                      0
                      
                     )
pbp['FT5'] = np.where(pbp.OREB_outcome == 6,
                     np.where(((pbp.seven_next_play_event_type == 3) & np.logical_not(pbp.seven_next_Home_desc.str.contains('MISS')) 
                               & (pd.notnull(pbp.HOMEDESCRIPTION))) |
                              ((pbp.seven_next_play_event_type == 3) & np.logical_not(pbp.seven_next_Visitor_desc.str.contains('MISS'))
                               & (pd.notnull(pbp.VISITORDESCRIPTION))),
                             1,
                             0),
                      0
                      
                     )

pbp['FT_PTS'] = pbp.FT1 + pbp.FT2 + pbp.FT3 + pbp.FT4 + pbp.FT5
pbp['two_next_shot_value'] = np.where((pbp.OREB_outcome == 1),
                                       np.where(((pbp.two_next_Home_desc.str.contains('3PT')) & (pd.notnull(pbp.HOMEDESCRIPTION))) |
                                                ((pbp.two_next_Visitor_desc.str.contains('3PT'))& (pd.notnull(pbp.VISITORDESCRIPTION))),
                                                  3,
                                                  2),
                                      pbp.FT_PTS)
            


In [44]:
pbp

Unnamed: 0   GAME_ID  EVENTNUM  EVENTMSGTYPE  EVENTMSGACTIONTYPE  \
0                0  21800001         4            10                   0   
1                1  21800001         7             2                   1   
2                2  21800001         8             4                   0   
3                3  21800001        10             2                   1   
4                4  21800001        11             4                   0   
5                5  21800001        12             5                   1   
6                6  21800001        14             2                  41   
7                7  21800001        16             4                   0   
8                8  21800001        17             1                  41   
9                9  21800001        19             2                   6   
10              10  21800001        20             4                   0   
11              11  21800001        21             2                  79   
12              12  21800001        22             4                   0   
13              13  21800001        23             2                  73   
14              14  21800001        24             4                   0   
15              15  21800001        25             2                   6   
16              16  21800001        26             4                   0   
17              17  21800001        27             2                  41   
18              18  21800001        28             4                   0   
19              19  21800001        29             2                  41   
20              20  21800001        30             4                   0   
21              21  21800001        31             5                  39   
22              22  21800001        32             2                   5   
23              23  21800001        34             4                   0   
24              24  21800001        35             2                  72   
25              25  21800001        36             4                   0   
26              26  21800001        38             1                  79   
27              27  21800001        40             6                   1   
28              28  21800001        42             2                  79   
29              29  21800001        43             4                   0   
30              30  21800001        44             1                  98   
31              31  21800001        46             2                  80   
32              32  21800001        47             4                   0   
33              33  21800001        48             1                   1   
34              34  21800001        50             1                   6   
35              35  21800001        51             6                   1   
36              36  21800001        53             2                  80   
37              37  21800001        54             4                   0   
38              38  21800001        55             1                  63   
39              39  21800001        56             1                  80   
40              40  21800001        58             5                   8   
41              41  21800001        59             2                   1   
42              42  21800001        60             4                   0   
43              43  21800001        61             2                  79   
44              44  21800001        62             4                   0   
45              45  21800001        63             2                   6   
46              46  21800001        65             4                   0   
47              47  21800001        66             9                   1   
48              48  21800001        67             8                   0   
49              49  21800001        68             8                   0   
50              50  21800001        71             5                   1   
51              51  21800001        73             6    

In [65]:
# per stats from https://stats.nba.com/teams/misc/?sort=TEAM_NAME&dir=-1&Season=2018-19&SeasonType=Regular%20Season&PerMode=Totals&DateTo=12%2F24%2F2018
# actual 2nd chance points = 13050
print("My 2nd chance points", pbp.two_next_shot_value.sum())
pbp.two_next_shot_value.sum()/13050

My 2nd chance points 10318


0.7906513409961686

In [64]:
#  per stats from https://stats.nba.com/teams/traditional/?sort=OREB&dir=-1&Season=2018-19&SeasonType=Regular%20Season&PerMode=Totals&DateTo=12%2F24%2F2018
# actual total OREB = 10273
print(pbp.creates_OREB.sum())
pbp.creates_OREB.sum()/10273

10196


0.9925046237710503

### Merge shotcharts and pbp data
Merge shots with pbp on `GAME_ID` and `EVENTNUM`

In [46]:
shotsPBP = shots.merge(pbp, left_on=["GAME_ID","GAME_EVENT_ID"], right_on=["GAME_ID","EVENTNUM"])


In [47]:
shotsPBP['combined_zone']=shotsPBP['SHOT_ZONE_BASIC']+'_'+shotsPBP['SHOT_ZONE_AREA']+'_'+shotsPBP['SHOT_ZONE_RANGE']+'_'+shotsPBP['SHOT_TYPE']
shotsPBP = shotsPBP[shotsPBP.SHOT_ZONE_RANGE != "Back Court Shot"]
uniquezones = shotsPBP.combined_zone.unique()
uniquezones.sort()
print(uniquezones)
print(uniquezones.shape)

['Above the Break 3_Center(C)_24+ ft._2PT Field Goal'
 'Above the Break 3_Center(C)_24+ ft._3PT Field Goal'
 'Above the Break 3_Left Side Center(LC)_24+ ft._2PT Field Goal'
 'Above the Break 3_Left Side Center(LC)_24+ ft._3PT Field Goal'
 'Above the Break 3_Right Side Center(RC)_24+ ft._2PT Field Goal'
 'Above the Break 3_Right Side Center(RC)_24+ ft._3PT Field Goal'
 'In The Paint (Non-RA)_Center(C)_8-16 ft._2PT Field Goal'
 'In The Paint (Non-RA)_Center(C)_Less Than 8 ft._2PT Field Goal'
 'In The Paint (Non-RA)_Left Side(L)_8-16 ft._2PT Field Goal'
 'In The Paint (Non-RA)_Right Side(R)_8-16 ft._2PT Field Goal'
 'Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal'
 'Mid-Range_Center(C)_16-24 ft._2PT Field Goal'
 'Mid-Range_Center(C)_8-16 ft._2PT Field Goal'
 'Mid-Range_Left Side Center(LC)_16-24 ft._2PT Field Goal'
 'Mid-Range_Left Side Center(LC)_16-24 ft._3PT Field Goal'
 'Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal'
 'Mid-Range_Left Side(L)_16-24 ft._3PT Field Goal'
 'Mid-Range_

Clean up weird shot zones such as midrange 3PT and ATB 2PT

In [48]:


shotsPBP.loc[shotsPBP.combined_zone == 'Above the Break 3_Center(C)_24+ ft._2PT Field Goal', "combined_zone"] = 'Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal'
shotsPBP.loc[shotsPBP.combined_zone == 'Above the Break 3_Left Side Center(LC)_24+ ft._2PT Field Goal', "combined_zone"] = 'Mid-Range_Left Side Center(LC)_16-24 ft._2PT Field Goal'

shotsPBP.loc[shotsPBP.combined_zone == 'Above the Break 3_Right Side Center(RC)_24+ ft._2PT Field Goal', "combined_zone"] = 'Mid-Range_Right Side Center(RC)_16-24 ft._2PT Field Goal'
shotsPBP.loc[shotsPBP.combined_zone == 'Mid-Range_Left Side Center(LC)_16-24 ft._3PT Field Goal', "combined_zone"] = 'Above the Break 3_Left Side Center(LC)_24+ ft._3PT Field Goal'
shotsPBP.loc[shotsPBP.combined_zone == 'Mid-Range_Left Side(L)_16-24 ft._3PT Field Goal', "combined_zone"] = 'Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal'
shotsPBP.loc[shotsPBP.combined_zone == 'Mid-Range_Right Side Center(RC)_16-24 ft._3PT Field Goal', "combined_zone"] = 'Above the Break 3_Right Side Center(RC)_24+ ft._3PT Field Goal'
shotsPBP.loc[shotsPBP.combined_zone == 'Mid-Range_Right Side(R)_16-24 ft._3PT Field Goal', "combined_zone"] = 'Right Corner 3_Right Side(R)_24+ ft._3PT Field Goal'



In [49]:
uniquezones = shotsPBP.combined_zone.unique()
uniquezones.sort()
print(uniquezones)
print(uniquezones.shape)

['Above the Break 3_Center(C)_24+ ft._3PT Field Goal'
 'Above the Break 3_Left Side Center(LC)_24+ ft._3PT Field Goal'
 'Above the Break 3_Right Side Center(RC)_24+ ft._3PT Field Goal'
 'In The Paint (Non-RA)_Center(C)_8-16 ft._2PT Field Goal'
 'In The Paint (Non-RA)_Center(C)_Less Than 8 ft._2PT Field Goal'
 'In The Paint (Non-RA)_Left Side(L)_8-16 ft._2PT Field Goal'
 'In The Paint (Non-RA)_Right Side(R)_8-16 ft._2PT Field Goal'
 'Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal'
 'Mid-Range_Center(C)_16-24 ft._2PT Field Goal'
 'Mid-Range_Center(C)_8-16 ft._2PT Field Goal'
 'Mid-Range_Left Side Center(LC)_16-24 ft._2PT Field Goal'
 'Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal'
 'Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal'
 'Mid-Range_Right Side Center(RC)_16-24 ft._2PT Field Goal'
 'Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal'
 'Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal'
 'Restricted Area_Center(C)_Less Than 8 ft._2PT Field Goal'
 'Right Corner 3_Right Side(R)_24+

### Calculate FG% for each zone
1. Sum `SHOT_ATTEMPTED_FLAG` for each zone to get FGA
2. Sum `SHOT_MADE_FLAG` for each zone to get FGM
3. Calculate FGM/FGA for each zone
1. Sum `creates_OREB` for each zone
2. Sum misses for each zone (FGA - FGM)
3. Calculate OREB%
4. Calculate `pts_per_OREB`
5. Calculate `xpps = ` $FG\% \times shot\_value + OREB\% \times pts\_per\_OREB$

In [54]:
league_by_zone = shotsPBP.groupby(by="combined_zone", as_index=False).agg({"SHOT_TYPE":"max",
                                                                           "SHOT_MADE_FLAG":"sum",
                                                                            "SHOT_ATTEMPTED_FLAG": "sum",
                                                                           "creates_OREB": "sum",
                                                                                    "two_next_shot_value":"sum"})

league_by_zone.rename(columns={"SHOT_ATTEMPTED_FLAG": "FGA",
                               "creates_OREB": "OREB",
                        "SHOT_MADE_FLAG":"FGM",
                            "two_next_shot_value":"2nd_Chance_Pts"}, inplace=True)
league_by_zone.fillna(0, inplace=True)
league_by_zone["FG%"] = league_by_zone.FGM/league_by_zone.FGA
league_by_zone["MISSES"] = league_by_zone.FGA - league_by_zone.FGM
league_by_zone["OREB%"] = league_by_zone.OREB/league_by_zone.MISSES
league_by_zone["shot_value"] = np.where(league_by_zone.SHOT_TYPE.str.contains('2PT') ,2,3)
league_by_zone["pts_per_OREB"] = league_by_zone["2nd_Chance_Pts"]/league_by_zone["OREB"]
league_by_zone.fillna(0, inplace=True)
league_by_zone['xpps'] = league_by_zone["FG%"] * league_by_zone.shot_value + (1- league_by_zone['FG%'])*league_by_zone["OREB%"]*league_by_zone.pts_per_OREB

league_by_zone.sort_values("xpps", ascending=False)

combined_zone       SHOT_TYPE    FGM  \
16  Restricted Area_Center(C)_Less Than 8 ft._2PT ...  2PT Field Goal  18228   
7   Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal  3PT Field Goal   1374   
17  Right Corner 3_Right Side(R)_24+ ft._3PT Field...  3PT Field Goal   1256   
2   Above the Break 3_Right Side Center(RC)_24+ ft...  3PT Field Goal   2977   
1   Above the Break 3_Left Side Center(LC)_24+ ft....  3PT Field Goal   3125   
0   Above the Break 3_Center(C)_24+ ft._3PT Field ...  3PT Field Goal   2099   
3   In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...  2PT Field Goal   1905   
5   In The Paint (Non-RA)_Left Side(L)_8-16 ft._2P...  2PT Field Goal    320   
9         Mid-Range_Center(C)_8-16 ft._2PT Field Goal  2PT Field Goal    412   
15    Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal  2PT Field Goal    920   
4   In The Paint (Non-RA)_Center(C)_Less Than 8 ft...  2PT Field Goal   2953   
6   In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...  2PT Field Goal    303   
13  Mid-Range_Right Side Center(RC)_16-24 ft._2PT ...  2PT Field Goal    948   
12     Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal  2PT Field Goal    872   
8        Mid-Range_Center(C)_16-24 ft._2PT Field Goal  2PT Field Goal    970   
10  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...  2PT Field Goal    862   
11    Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal  2PT Field Goal    318   
14   Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal  2PT Field Goal    316   

      FGA  OREB  2nd_Chance_Pts       FG%  MISSES     OREB%  shot_value  \
16  29052  3139            3428  0.627427   10824  0.290004           2   
7    3541   405             385  0.388026    2167  0.186894           3   
17   3334   405             421  0.376725    2078  0.194899           3   
2    8476   986             943  0.351227    5499  0.179305           3   
1    8968  1008             997  0.348461    5843  0.172514           3   
0    6260   627             594  0.335304    4161  0.150685           3   
3    4578   582             565  0.416121    2673  0.217733           2   
5     814   113             131  0.393120     494  0.228745           2   
9     966    97              87  0.426501     554  0.175090           2   
15   2189   227             216  0.420283    1269  0.178881           2   
4    7683  1248            1268  0.384355    4730  0.263848           2   
6     782   120             109  0.387468     479  0.250522           2   
13   2296   196             201  0.412892    1348  0.145401           2   
12   2208   240             242  0.394928    1336  0.179641           2   
8    2377   186             179  0.408077    1407  0.132196           2   
10   2123   168             160  0.406029    1261  0.133228           2   
11    822    85              87  0.386861     504  0.168651           2   
14    789    68              57  0.400507     473  0.143763           2   

    pts_per_OREB      xpps  
16      1.092068  1.372849  
7       0.950617  1.272804  
17      1.039506  1.256449  
2       0.956389  1.164936  
1       0.989087  1.156557  
0       0.947368  1.100799  
3       0.970790  0.955657  
5       1.159292  0.947174  
9       0.896907  0.943064  
15      0.951542  0.939242  
4       1.016026  0.933750  
6       0.908333  0.914322  
13      1.025510  0.913328  
12      1.008333  0.899457  
8       0.962366  0.891460  
10      0.952381  0.887423  
11      1.023529  0.879562  
14      0.838235  0.873257

In [55]:
league_by_zone['2nd_Chance_Pts'].sum()

10070

In [56]:
team_by_zone = shotsPBP.groupby(by=["TEAM_ID","combined_zone"], as_index=False).agg({"SHOT_TYPE":"max",
                                                                                     "TEAM_NAME": "max",
                                                                           "SHOT_MADE_FLAG":"sum",
                                                                            "SHOT_ATTEMPTED_FLAG": "sum",
                                                                           "creates_OREB": "sum",
                                                                                    "two_next_shot_value":"sum"})

team_by_zone.rename(columns={"SHOT_ATTEMPTED_FLAG": "FGA",
                               "creates_OREB": "OREB",
                        "SHOT_MADE_FLAG":"FGM",
                            "two_next_shot_value":"2nd_Chance_Pts"}, inplace=True)
team_by_zone.fillna(0, inplace=True)
team_by_zone["FG%"] = team_by_zone.FGM/team_by_zone.FGA
team_by_zone["MISSES"] = team_by_zone.FGA - team_by_zone.FGM
team_by_zone["OREB%"] = team_by_zone.OREB/team_by_zone.MISSES
team_by_zone["shot_value"] = np.where(team_by_zone.SHOT_TYPE.str.contains('2PT') ,2,3)
team_by_zone["pts_per_OREB"] = team_by_zone["2nd_Chance_Pts"]/team_by_zone["OREB"]
team_by_zone.fillna(0, inplace=True)
team_by_zone['xpps'] = team_by_zone["FG%"] * team_by_zone.shot_value + (1- team_by_zone['FG%'])*team_by_zone["OREB%"]*team_by_zone.pts_per_OREB

team_by_zone

TEAM_ID                                      combined_zone  \
0    1610612737  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
1    1610612737  Above the Break 3_Left Side Center(LC)_24+ ft....   
2    1610612737  Above the Break 3_Right Side Center(RC)_24+ ft...   
3    1610612737  In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...   
4    1610612737  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
5    1610612737  In The Paint (Non-RA)_Left Side(L)_8-16 ft._2P...   
6    1610612737  In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...   
7    1610612737  Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal   
8    1610612737       Mid-Range_Center(C)_16-24 ft._2PT Field Goal   
9    1610612737        Mid-Range_Center(C)_8-16 ft._2PT Field Goal   
10   1610612737  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...   
11   1610612737    Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal   
12   1610612737     Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal   
13   1610612737  Mid-Range_Right Side Center(RC)_16-24 ft._2PT ...   
14   1610612737   Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal   
15   1610612737    Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal   
16   1610612737  Restricted Area_Center(C)_Less Than 8 ft._2PT ...   
17   1610612737  Right Corner 3_Right Side(R)_24+ ft._3PT Field...   
18   1610612738  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
19   1610612738  Above the Break 3_Left Side Center(LC)_24+ ft....   
20   1610612738  Above the Break 3_Right Side Center(RC)_24+ ft...   
21   1610612738  In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...   
22   1610612738  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
23   1610612738  In The Paint (Non-RA)_Left Side(L)_8-16 ft._2P...   
24   1610612738  In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...   
25   1610612738  Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal   
26   1610612738       Mid-Range_Center(C)_16-24 ft._2PT Field Goal   
27   1610612738        Mid-Range_Center(C)_8-16 ft._2PT Field Goal   
28   1610612738  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...   
29   1610612738    Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal   
30   1610612738     Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal   
31   1610612738  Mid-Range_Right Side Center(RC)_16-24 ft._2PT ...   
32   1610612738   Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal   
33   1610612738    Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal   
34   1610612738  Restricted Area_Center(C)_Less Than 8 ft._2PT ...   
35   1610612738  Right Corner 3_Right Side(R)_24+ ft._3PT Field...   
36   1610612739  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
37   1610612739  Above the Break 3_Left Side Center(LC)_24+ ft....   
38   1610612739  Above the Break 3_Right Side Center(RC)_24+ ft...   
39   1610612739  In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...   
40   1610612739  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
41   1610612739  In The Paint (Non-RA)_Left Side(L)_8-16 ft._2P...   
42   1610612739  In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...   
43   1610612739  Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal   
44   1610612739       Mid-Range_Center(C)_16-24 ft._2PT Field Goal   
45   1610612739        Mid-Range_Center(C)_8-16 ft._2PT Field Goal   
46   1610612739  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...   
47   1610612739    Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal   
48   1610612739     Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal   
49   1610612739  Mid-Range_Right Side Center(RC)_16-24 ft._2PT ...   
50   1610612739   Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal   
51   1610612739    Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal   
52   1610612739  Restricted Area_Center(C)_Less Than 8 ft._2PT ...   
53   1610612739  Right Corner 3_Right Side(R)_24+ ft._3PT Field...   
54   1610612740  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
55   1610612740  Above the Break 3_Left Side Center(LC)_24+ ft....   
56   1610612740  A

In [57]:
team_by_zone.groupby('TEAM_NAME')['OREB'].sum()

TEAM_NAME
Atlanta Hawks             330
Boston Celtics            330
Brooklyn Nets             390
Charlotte Hornets         299
Chicago Bulls             244
Cleveland Cavaliers       370
Dallas Mavericks          321
Denver Nuggets            367
Detroit Pistons           351
Golden State Warriors     330
Houston Rockets           337
Indiana Pacers            306
LA Clippers               307
Los Angeles Lakers        314
Memphis Grizzlies         247
Miami Heat                387
Milwaukee Bucks           304
Minnesota Timberwolves    348
New Orleans Pelicans      374
New York Knicks           382
Oklahoma City Thunder     391
Orlando Magic             281
Philadelphia 76ers        338
Phoenix Suns              296
Portland Trail Blazers    366
Sacramento Kings          326
San Antonio Spurs         322
Toronto Raptors           341
Utah Jazz                 305
Washington Wizards        296
Name: OREB, dtype: int64

In [58]:
player_by_zone = shotsPBP.groupby(by=["PLAYER_NAME","combined_zone"], as_index=False).agg({"SHOT_TYPE":"max",
                                                                                           "TEAM_NAME": "max",
                                                                                           "TEAM_ID": "max",
                                                                                           "PLAYER_ID": "max",
                                                                           "SHOT_MADE_FLAG":"sum",
                                                                            "SHOT_ATTEMPTED_FLAG": "sum",
                                                                           "creates_OREB": "sum",
                                                                                          "two_next_shot_value":"sum"})

player_by_zone.rename(columns={"SHOT_ATTEMPTED_FLAG": "FGA",
                               "creates_OREB": "OREB",
                        "SHOT_MADE_FLAG":"FGM",
                            "two_next_shot_value":"2nd_Chance_Pts"}, inplace=True)
player_by_zone.fillna(0, inplace=True)
player_by_zone["FG%"] = player_by_zone.FGM/player_by_zone.FGA
player_by_zone["MISSES"] = player_by_zone.FGA - player_by_zone.FGM
player_by_zone["OREB%"] = player_by_zone.OREB/player_by_zone.MISSES
player_by_zone["shot_value"] = np.where(player_by_zone.SHOT_TYPE.str.contains('2PT') ,2,3)
player_by_zone["pts_per_OREB"] = player_by_zone["2nd_Chance_Pts"]/player_by_zone["OREB"]
player_by_zone.fillna(0, inplace=True)
player_by_zone['xpps'] = player_by_zone["FG%"] * player_by_zone.shot_value + (1- player_by_zone['FG%'])*player_by_zone["OREB%"]*player_by_zone.pts_per_OREB

player_by_zone

PLAYER_NAME                                      combined_zone  \
0            Aaron Gordon  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
1            Aaron Gordon  Above the Break 3_Left Side Center(LC)_24+ ft....   
2            Aaron Gordon  Above the Break 3_Right Side Center(RC)_24+ ft...   
3            Aaron Gordon  In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...   
4            Aaron Gordon  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
5            Aaron Gordon  In The Paint (Non-RA)_Left Side(L)_8-16 ft._2P...   
6            Aaron Gordon  In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...   
7            Aaron Gordon  Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal   
8            Aaron Gordon       Mid-Range_Center(C)_16-24 ft._2PT Field Goal   
9            Aaron Gordon        Mid-Range_Center(C)_8-16 ft._2PT Field Goal   
10           Aaron Gordon  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...   
11           Aaron Gordon    Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal   
12           Aaron Gordon     Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal   
13           Aaron Gordon  Mid-Range_Right Side Center(RC)_16-24 ft._2PT ...   
14           Aaron Gordon   Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal   
15           Aaron Gordon    Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal   
16           Aaron Gordon  Restricted Area_Center(C)_Less Than 8 ft._2PT ...   
17           Aaron Gordon  Right Corner 3_Right Side(R)_24+ ft._3PT Field...   
18          Aaron Holiday  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
19          Aaron Holiday  Above the Break 3_Left Side Center(LC)_24+ ft....   
20          Aaron Holiday  Above the Break 3_Right Side Center(RC)_24+ ft...   
21          Aaron Holiday  In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...   
22          Aaron Holiday  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
23          Aaron Holiday  In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...   
24          Aaron Holiday  Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal   
25          Aaron Holiday       Mid-Range_Center(C)_16-24 ft._2PT Field Goal   
26          Aaron Holiday        Mid-Range_Center(C)_8-16 ft._2PT Field Goal   
27          Aaron Holiday  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...   
28          Aaron Holiday  Mid-Range_Right Side Center(RC)_16-24 ft._2PT ...   
29          Aaron Holiday   Mid-Range_Right Side(R)_16-24 ft._2PT Field Goal   
30          Aaron Holiday    Mid-Range_Right Side(R)_8-16 ft._2PT Field Goal   
31          Aaron Holiday  Restricted Area_Center(C)_Less Than 8 ft._2PT ...   
32          Aaron Holiday  Right Corner 3_Right Side(R)_24+ ft._3PT Field...   
33            Abdel Nader  Above the Break 3_Left Side Center(LC)_24+ ft....   
34            Abdel Nader  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
35            Abdel Nader  Restricted Area_Center(C)_Less Than 8 ft._2PT ...   
36            Abdel Nader  Right Corner 3_Right Side(R)_24+ ft._3PT Field...   
37             Al Horford  Above the Break 3_Center(C)_24+ ft._3PT Field ...   
38             Al Horford  Above the Break 3_Left Side Center(LC)_24+ ft....   
39             Al Horford  Above the Break 3_Right Side Center(RC)_24+ ft...   
40             Al Horford  In The Paint (Non-RA)_Center(C)_8-16 ft._2PT F...   
41             Al Horford  In The Paint (Non-RA)_Center(C)_Less Than 8 ft...   
42             Al Horford  In The Paint (Non-RA)_Right Side(R)_8-16 ft._2...   
43             Al Horford  Left Corner 3_Left Side(L)_24+ ft._3PT Field Goal   
44             Al Horford       Mid-Range_Center(C)_16-24 ft._2PT Field Goal   
45             Al Horford        Mid-Range_Center(C)_8-16 ft._2PT Field Goal   
46             Al Horford  Mid-Range_Left Side Center(LC)_16-24 ft._2PT F...   
47             Al Horford    Mid-Range_Left Side(L)_16-24 ft._2PT Field Goal   
48             Al Horford     Mid-Range_Left Side(L)_8-16 ft._2PT Field Goal   
49            

In [59]:
league_by_zone.to_csv("league-xpps.csv")

In [60]:
team_by_zone.to_csv("team-xpps.csv")

In [61]:
player_by_zone.to_csv("player-xpps.csv")